In [210]:
#!pip install folium

In [211]:
import folium
import pandas as pd

In [234]:
utah_df=pd.read_csv('1871-utah-postmaster-salaries.csv')
print(utah_df.sample(5))
utah_df.dtypes

        PO_Name     County State  PM_Salary   Latitude   Longitude
6   Bloomington   Richland    UT         12        NaN         NaN
23       Draper  Salt Lake    UT         39  40.357729 -111.862155
55        Kanab       Kane    UT         12  37.006375 -112.528536
51        Hyrum      Cache    UT         42  41.633822 -111.854110
68        Manti    Sanpete    UT        100  39.267462 -111.636585


PO_Name       object
County        object
State         object
PM_Salary      int64
Latitude     float64
Longitude    float64
dtype: object

In [213]:
utah_map_empty = folium.Map(location=[40, -111], zoom_start=6)
utah_map_empty

In [214]:
# Create a duplicate of our starting point map to start adding markers to
utah_map = utah_map_empty

folium.Marker(location=[38.41, -112.339], popup="Adamsville Post Office").add_to(utah_map)
utah_map

In [215]:
# We're going to define a function that creates an empty map that we will use to add our markers to. Each time we want to add markers, we can call this function to create an empty map
def create_empty_map():
    return folium.Map(location=[40, -111], zoom_start=6)

utah_map = create_empty_map()
utah_map

In [216]:
# Melanie Walsh function we will edit:
def create_map_markers(row, map_name):
    folium.Marker(location=[row['lat'], row['lon']], popup=row['place']).add_to(map_name)

In [217]:
def create_map_markers(row, map_name):
    folium.Marker(location=[row['Latitude'], row['Longitude']], popup=row['PO_Name']).add_to(map_name)

In [218]:
# Check for columns with missing values
missing_values = utah_df.isna().sum()
print(missing_values)

PO_Name      0
County       0
State        0
PM_Salary    0
Latitude     4
Longitude    4
dtype: int64


In [219]:
# Filter out post offices that are missing a latitude value
utah_df_locations = utah_df[utah_df['Latitude'].notna()]
print(len(utah_df))
print(len(utah_df_locations))

136
132


In [220]:
# Method 1: Using a for loop to iterate through our dataframe and add markers sequentially

# initialize an empty map
utah_map = create_empty_map()

# iterrows() allows you to loop through a dataframe row by row and return the index position + the row
for index, row in utah_df_locations.iterrows():
    print(f"Name of post office:", row[0])

#now let's iterate through and call our function for each row
for index, row in utah_df_locations.iterrows():
    create_map_markers(row, utah_map)

utah_map

Name of post office: Adamsville
Name of post office: Alma
Name of post office: Alpine City
Name of post office: American Fork
Name of post office: Bellevue
Name of post office: Bingham Canyon
Name of post office: Brigham City
Name of post office: Bullion
Name of post office: Cedar City
Name of post office: Cedar Valley
Name of post office: Centerville
Name of post office: Central City
Name of post office: Chicken Creek
Name of post office: Clarkston
Name of post office: Clifton
Name of post office: Clover Valley
Name of post office: Coalville
Name of post office: Corinne
Name of post office: Cove Creek
Name of post office: Croydon
Name of post office: Deseret
Name of post office: Diamond
Name of post office: Draper
Name of post office: Duncans Retreat
Name of post office: Echo City
Name of post office: Eden
Name of post office: Emmaville
Name of post office: Ephraim
Name of post office: Eureka
Name of post office: Fair View
Name of post office: Fairfield
Name of post office: Farmington

/var/folders/tv/dd7y76ys3zg57b4929sz1vnc0000gn/T/ipykernel_45076/444210454.py:8: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  print(f"Name of post office:", row[0])


In [221]:
# Method 2: Using .apply() to add markers with our function for all rows

# initialize an empty map
utah_map = utah_map_empty

# Now apply this function to each row in our filtered DataFrame
# For each row, we'll pass:
#   1. The row itself (handled automatically by .apply())
#   2. Our map object (we need to specify this explicitly)
#   3. The "axis" value for .apply() to indicate we want to process row by row

# .apply() allows you to apply a function to each row in the dataframe
utah_df_locations.apply(
    create_map_markers, # The function to apply
    map_name=utah_map,  # Additional argument to pass to the function
    axis='columns' # Process row by row instead of column by column
)

utah_map

In [222]:
# Melanie Walsh function we will edit:
def create_ICE_map_markers(row, map_name):
    folium.CircleMarker(location=[row['lat'], row['lon']], raidus=100, fill=True,
                popup=folium.Popup(f"{row['Name'].title()} <br> {row['City'].title()}, {row['State']}", max_width=200),
                  tooltip=f"{row['Name'].title()} <br> {row['City'].title()}, {row['State']}"
                 ).add_to(map_name)

In [223]:
def create_circle_markers(row, map_name):
    folium.CircleMarker(location=[row['Latitude'], row['Longitude']],
                        radius=40, 
                        fill=True,
                        popup=folium.Popup(f"{row['PO_Name'].title()}", max_width=200),
                        tooltip=f"{row['PO_Name'].title()}"
                 ).add_to(map_name)

In [224]:
# initialize an empty map
utah_map = create_empty_map()

# call our function for each row
utah_df_locations.apply(create_circle_markers, map_name=utah_map, axis="columns")

utah_map

In [249]:
# alter map appearance
def create_circle_markers(row, map_name):
    folium.CircleMarker(location=[row['Latitude'], row['Longitude']],
                        radius=8,
                        color = 'green',
                        fill=True,
                        fill_color='green',
                        fill_opacity=0.6,
                        popup=folium.Popup(f"Post Office: {row['PO_Name'].title()}", max_width=200),
                        tooltip=f"Postmaster Salary: ${row['PM_Salary']}"
                 ).add_to(map_name)

In [250]:
# initialize an empty map
utah_map = create_empty_map()

# call our function for each row
utah_df_locations.apply(
    create_circle_markers, # The function to apply
    map_name=utah_map,  # Additional argument to pass to the function
    axis='columns' # Process row by row instead of column by column
)

utah_map


In [251]:
# make new function to create circle markers sized by postmaster salary
def create_sized_circle_markers(row, map_name):
    folium.CircleMarker(location=[row['Latitude'], row['Longitude']],
                        radius=row['PM_Salary'],
                        fill=True,
                        popup=folium.Popup(f"Post Office: {row['PO_Name'].title()}", max_width=200),
                        tooltip=f"Postmaster Salary: ${row['PM_Salary']}"
                 ).add_to(map_name)

In [252]:
# initialize an empty map
utah_map = create_empty_map()

# call our function for each row
utah_df_locations.apply(
    create_sized_circle_markers, # The function to apply
    map_name=utah_map,  # Additional argument to pass to the function
    axis='columns' # Process row by row instead of column by column
)

utah_map

In [255]:
# make new function to create circle markers sized by postmaster salary - this time adjusting the radius size in pixels to make it more legible
def create_sized_circle_markers(row, map_name):
    folium.CircleMarker(location=[row['Latitude'], row['Longitude']],
                        radius=row['PM_Salary']/100,
                        fill=True,
                        popup=folium.Popup(f"Post Office: {row['PO_Name'].title()}", max_width=200),
                        tooltip=f"Postmaster Salary: ${row['PM_Salary']}"
                 ).add_to(map_name)

In [256]:
# initialize an empty map
utah_map = create_empty_map()

# call our function for each row
utah_df_locations.apply(
    create_sized_circle_markers, # The function to apply
    map_name=utah_map,  # Additional argument to pass to the function
    axis='columns' # Process row by row instead of column by column
)

utah_map

In [ ]:
utah_df_locations.describe()

PM_Salary    Latitude   Longitude
count   132.000000  132.000000  132.000000
mean    101.098485   39.907743 -112.161190
std     344.225580    1.505091    0.593117
min       4.000000   37.006375 -113.819415
25%      12.000000   38.874099 -112.379230
50%      22.000000   40.380926 -111.973830
75%      70.000000   41.080917 -111.819912
max    3600.000000   42.187500 -111.281850

In [ ]:
def add_salary_buckets(salary):
    # Create a new column for the salary bucket
    if salary < 50:
        bucket = 'Low Salary'
    elif salary >= 50 and salary < 250:
        bucket = 'Medium Salary'
    elif salary >= 250 and salary < 1000:
        bucket = 'High Salary'
    else:
        bucket = 'Very High Salary'
    return bucket

#test out the function
add_salary_buckets(2000)

'Very High Salary'

In [257]:
utah_df_locations['Salary_Bucket']=utah_df_locations['PM_Salary'].apply(add_salary_buckets) 
utah_df_locations.head()


PO_Name      County State  PM_Salary   Latitude   Longitude  \
0     Adamsville      Beaver    UT         10  38.258303 -112.793835   
1           Alma       Weber    UT         12  41.248833 -112.078275   
2    Alpine City        Utah    UT         27  40.453283 -111.777986   
3  American Fork        Utah    UT        130  40.375229 -111.796320   
4       Bellevue  Washington    UT         20  37.340815 -113.274116   

   Salary_Bucket  
0     Low Salary  
1     Low Salary  
2     Low Salary  
3  Medium Salary  
4     Low Salary

In [258]:
# create a function to add marker sizes based on the salary bucket
def add_marker_sizes(category):
    if category == 'Low Salary':
        return 4
    elif category == 'Medium Salary':
        return 8
    elif category == 'High Salary':
        return 12
    else: 
        return 16
    
#test out the function
add_marker_sizes('High Salary')

12

In [259]:
utah_df_locations['Marker_Size']=utah_df_locations['Salary_Bucket'].apply(add_marker_sizes)
utah_df_locations.head(10)

PO_Name      County State  PM_Salary   Latitude   Longitude  \
0       Adamsville      Beaver    UT         10  38.258303 -112.793835   
1             Alma       Weber    UT         12  41.248833 -112.078275   
2      Alpine City        Utah    UT         27  40.453283 -111.777986   
3    American Fork        Utah    UT        130  40.375229 -111.796320   
4         Bellevue  Washington    UT         20  37.340815 -113.274116   
5   Bingham Canyon   Salt Lake    UT         12  40.541613 -112.147997   
7     Brigham City   Box Elder    UT        400  41.510213 -112.015501   
8          Bullion       Piute    UT         12  38.410000 -112.339000   
9       Cedar City        Iron    UT        200  37.676644 -113.057171   
10    Cedar Valley        Utah    UT         13  40.327171 -112.104385   

    Salary_Bucket  Marker_Size  
0      Low Salary            4  
1      Low Salary            4  
2      Low Salary            4  
3   Medium Salary            8  
4      Low Salary            4  
5      Low Salary            4  
7     High Salary           12  
8      Low Salary            4  
9   Medium Salary            8  
10     Low Salary            4

In [270]:
# make new function to create circle markers sized by salary category
def create_sized_circle_markers(row, map_name):
    folium.CircleMarker(location=[row['Latitude'], row['Longitude']],
                        radius=row['Marker_Size'],
                        fill=True,
                        opacity=0.6,
                        popup=folium.Popup(f"Post Office: {row['PO_Name'].title()}", max_width=200),
                        tooltip=f"Postmaster Salary: ${row['PM_Salary']}"
                 ).add_to(map_name)

In [271]:
# initialize an empty map
utah_map = create_empty_map()

# call our function for each row
utah_df_locations.apply(
    create_sized_circle_markers, # The function to apply
    map_name=utah_map,  # Additional argument to pass to the function
    axis='columns' # Process row by row instead of column by column
)

utah_map

In [ ]:
#add in county boundaries
utah_counties = 'utah-counties-modern.geojson'

In [307]:
# initialize an empty map
utah_map = create_empty_map()

folium.GeoJson(utah_counties, zoom_on_click=True).add_to(utah_map)

utah_map

In [ ]:
utah_counties = folium.GeoJson('utah-counties-modern.geojson')

# Convert the GeoJson object to a GeoDataFrame
utah_counties_gdf = gpd.GeoDataFrame.from_features(utah_counties.data['features'])

# Display the GeoDataFrame
print(utah_counties_gdf.head())

                                            geometry  OBJECTID COUNTYNBR  \
0  POLYGON ((-112.15617 41.99773, -112.15399 41.9...         1        03   
1  POLYGON ((-110.25174 40.83235, -110.25071 40.8...         2        07   
2  POLYGON ((-111.99472 41.15267, -111.98778 41.1...         3        06   
3  POLYGON ((-112.23855 39.55363, -112.23597 39.5...         4        14   
4  POLYGON ((-111.39573 40.69019, -111.39561 40.6...         5        26   

    ENTITYNBR  ENTITYYR      NAME  FIPS STATEPLANE  POP_LASTCENSUS  \
0  2010031010      2010     CACHE     5      North          133154   
1  2010071010      2010  DUCHESNE    13    Central           19596   
2  2010061010      2010     DAVIS    11      North          362679   
3  2010141010      2010   MILLARD    27    Central           12975   
4  2010261010      2010   WASATCH    51    Central           34788   

   POP_CURRESTIMATE                              GlobalID FIPS_STR  COLOR4  
0            140173  ad3015be-b3c9-4316-b8dc-

AttributeError: 'GeoJson' object has no attribute 'dtypes'

In [320]:
county_counts = utah_df_locations['County'].value_counts().reset_index()
county_counts['County']=county_counts['County'].str.upper()
county_counts.rename(columns={'County': 'NAME'}, inplace=True)
county_counts

NAME  count
0   WASHINGTON     17
1        CACHE     14
2         UTAH     13
3        WEBER     12
4    SALT LAKE     10
5      MILLARD      8
6      SANPETE      8
7         JUAB      7
8         IRON      6
9       SUMMIT      6
10      TOOELE      5
11   BOX ELDER      5
12       DAVIS      5
13        KANE      3
14     WASATCH      3
15      SEVIER      3
16      MORGAN      3
17      BEAVER      2
18       PIUTE      1
19    RICHLAND      1

In [323]:
# initialize an empty map
utah_map = create_empty_map()

folium.Choropleth(
    geo_data = utah_counties,
    name = 'choropleth',
    #data = county_counts,
    #columns = ['NAME', 'count'],
    #key_on = 'NAME',
    fill_color = 'GnBu',
    line_opacity = 0.2,
    legend_name= 'number of post offices'
).add_to(utah_map)

utah_map

ValueError: Cannot render objects with any missing geometries: <folium.features.GeoJson object at 0x30eef30b0>